This notebook takes care of cuda out of memory errors, and uses multithreading to run inferences in parallel.
Now go run some experiments and share them with us. 

Have fun :)

- Ripes & Subz

NOTE: This notebook won't work if your model is trained on sovits 4.0-v2

__Join the Discord__: https://discord.gg/aihub

# Important Read Before Starting!!!
### **Quick Disclaimer ignore if you never ran Colab 2.0/2.2**
For those that have used [Colab 2.0,](https://colab.research.google.com/drive/1rKEqpU-HgxUwRhzCRIPO5P5InI26A4UZ) If you have **so-vits-svc-fork shortcut** from that colab delete it, or else it will try to load those models instead of yours

For those that have already used [Colab 2.2,](https://colab.research.google.com/drive/1n-lGFGIrkJfV38G980sqmAa_5nLAzzj_?usp=sharing) if you have a **models** **shortcut** from that colab with models already in it, delete it to avoid confusion

### **Prerequisites**

You need to create a folder named "models" exactly in your Google Drive. 

For a list of trained models you can download, go to the #models channel in the Discord. All you have to do is download one of them and upload the unzipped folder to your Google Drive. If your model folder that you downloaded contains a D_xxxx.pth file, you should delete it. It takes up unnecessary space in your Google Drive inside the "models" folders.

If you're using a model you trained yourself, put your config.json and G_xxxx.pth file in a folder and upload that to Google Drive inside the "models" folder.



Your google drive should [look like this](https://cdn.loom.com/images/originals/bdd3cf800a4d473fa9dfe3fb4c440d80.jpg?Policy=eyJTdGF0ZW1lbnQiOlt7IlJlc291cmNlIjoiaHR0cHM6Ly9jZG4ubG9vbS5jb20vaW1hZ2VzL29yaWdpbmFscy9iZGQzY2Y4MDBhNGQ0NzNmYTlkZmUzZmI0YzQ0MGQ4MC5qcGciLCJDb25kaXRpb24iOnsiRGF0ZUxlc3NUaGFuIjp7IkFXUzpFcG9jaFRpbWUiOjE2ODE4MzIxNjN9fX1dfQ__&Key-Pair-Id=APKAJQIC5BGSW7XXK7FQ&Signature=ofVFsEgL3MvlrUapn%7E2tccT9PRIpY4Jk%7E%7E8CiyXbbzEaNu9aFTzaJn5Rj6ic0rvqswzcYLc6bq5zTikNRlybRc22NFidfQr3%7E0wivduOTVU3-GN6YhySkT4toYoqnCbm1TZ-GLq3qlf-kljiYGeEQqu5I6JXPx9VsDWVxoyN3Qk5bwkbwXLGWTCA%7EZFLI-gK7H2gIkpgFrMeYB067FppJl2tnw7ttCFO2oNCILwvD4HDEMyrlfT1PsSlFxjpRB5Mv0ysHAtwDeQq3CumJyYzOUm6p7ML5lmqb1y8UD3YsoYkEgacm4kwm9G7OulmqwtNcPYRT90iS14gkn6RUuY69w__), and inside the models folder you should place the model for any artist you want to clone. Make sure the folder name has no spaces. For example if you downloaded the Ariana model then you should place that Ariana folder inside of the models folder [like this](https://media.discordapp.net/attachments/693349673620209724/1098536049761865790/opera_7XV5yBcjBE.png)

### **YeezyBeaver Notes**

Make sure there are no spaces/special characters in the folder name you make. For example A$AP Rocky folder should be named ASAPRocky.

If you plan on having a large number of models with this colab, take note of the speaker name at the bottom of the config.json file in your voice model folder, change that if its something that would not help you identify which model you are using.

With this colab you will only need to upload your models once inside the model folder and they will reload anytime you decide to run this colab again. If you add a new model folder mid session just re-run the last cell and it should be included as an option.

### **If you still aren't understanding here is VERY rough tutorial I made, someone please make a better one and I will update this video link**

https://www.youtube.com/watch?v=asDIG7Qvjgw

In [ ]:
#@title Setup: Run this cell to install sovits and connect your Google Drive
#@markdown ### If this cell take more than 5 minutes to get a green checkmark, press it again to stop, then press it again to restart.

!python -m pip install -U -q pip wheel &> /dev/null
%pip install -U -q ipython &> /dev/null
%pip install -U -q so-vits-svc-fork &> /dev/null

from google.colab import drive
drive.mount('/content/drive', force_remount=True)

In [ ]:
#@title Local Downloads: Run this cell to download and unzip

#@markdown ## Go into models folder and rename folder without spaces or special characters or inference won't work.

#@markdown Only huggingface/direct download links atm.
import urllib.request
from urllib.parse import urlsplit
import os, re

# set the URL for the file download
model_url = "https://huggingface.co/QuickWick/Music-AI-Voices/resolve/main/Michael%20Jackson%2083k/Michael%20Jackson%2083k.zip" #@param {"type": "string"}

# set the destination file path and filename
isExist = os.path.exists("/content/zips/")
if not isExist:
    os.mkdir("/content/zips/")
output_path = "/content/zips/"
filename = urlsplit(model_url).path.split("/")[-1]
print(filename)

# download the file using urllib.request.urlretrieve()
print("Downloading zip")
urllib.request.urlretrieve(model_url, output_path + filename)
with urllib.request.urlopen(model_url) as response, open(output_path + filename, 'wb') as outfile:
    data = response.read()
    outfile.write(data)
    
# extract the zip to local models folder
isExist = os.path.exists("/content/models/")
if not isExist:
    os.mkdir("/content/models/")
os.chdir('/content/zips/')
print("Extracting zip")
!unzip -q -n "/content/zips/{filename}" -d /content/models/
print("Extraction complete")

In [ ]:
#@title Open the file explorer on the left of your screen and drag-and-drop an audio file anywhere. Then run the below cell.

#@markdown ### If you get an error make sure there are no spaces/special characters in model folder name and the file name you uploaded

#@markdown ### Also make sure you followed all instructions above before asking for help in the discord. Good Luck!

from ipywidgets import widgets
import copy
import json
import glob
import os
import time
import threading
from IPython.display import Audio, display
from pathlib import Path
import subprocess
import shutil


SEGMENT_LENGTH = 75

os.chdir('/content/')
MODELS_DIR = "local" #@param ["drive", "local"]
if MODELS_DIR == "drive":
  MODELS_DIR =  "/content/drive/MyDrive/models/"
elif MODELS_DIR == "local":
  MODELS_DIR = "/content/models/"

MUSIC_EXTENSIONS = ['.mp3', '.wav', '.flac', '.aac']

SEGMENTS_DIRNAME = f"segments"
INFERENCE_OUTPUT_DIRNAME = "inference_output"

def slice_audio(filepath, segment_length):
    assert os.path.exists(filepath), f"Could not find {filepath}. Make sure you've entered the correct filename."
    # Get the filename and extension of the input file
    filename, extension = os.path.splitext(filepath)
    filename = filename.split("/")[-1]

    os.makedirs(SEGMENTS_DIRNAME, exist_ok=True)

    # Set the output filename pattern
    output_pattern = f"{SEGMENTS_DIRNAME}/{filename}_%d{extension}"

    # Use ffmpeg to split the audio into segments
    os.system(f"ffmpeg -i {filepath} -f segment -segment_time {segment_length} -c copy {output_pattern}")


def get_container_format(filename):
    command = ["ffprobe", "-v", "error", "-select_streams", "v:0", "-show_entries", "format=format_name", "-of", "default=noprint_wrappers=1:nokey=1", filename]
    process = subprocess.Popen(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    output, error = process.communicate()
    if error:
        raise ValueError(f"Error getting container format: {error.decode()}")
    return output.decode().strip()

def run_inference(speaker, seg_path, f0_method, transpose, noise_scale, cluster_ratio):
    model_path = speaker["model_path"]
    config_path = speaker["cfg_path"]
    cluster_path = speaker["cluster_path"]

    inference_cmd = f"svc infer {seg_path.absolute()} -m {model_path} -c {config_path} {f'-k {cluster_path} -r {cluster_ratio}' if cluster_path != '' and cluster_ratio > 0 else ''} -t {transpose} --f0-method {f0_method} -n {noise_scale} -o {INFERENCE_OUTPUT_DIRNAME}/{seg_path.name} --no-auto-predict-f0"

    print(f"\nPerforming inference on... {seg_path.absolute()}\ninference cmd: {inference_cmd}", )
    result = subprocess.run(
          inference_cmd.split(),
          stdout=subprocess.PIPE,
          stderr=subprocess.PIPE,
          text=True
        )
    
    files_length = len(sorted(Path(SEGMENTS_DIRNAME).glob("*")))
    if result.stderr:
      if "AttributeError" in result.stderr:
        raise Exception(result.stderr + "Make sure your model is not 4.0-v2. This notebook only works on 4.0-v1 models.")
    if files_length == 0:
      raise Exception("An unknown error occured!")
      

def concatenate_segments(foldername, final_filename):
    foldername = Path(foldername)
    assert foldername.exists(), "folder doesnt exist. Enter correct foldername"
    all_segs = [f for f in sorted(foldername.glob("**/*")) if f.is_file()]
    # if len(all_segs) > 0:
    ext= all_segs[0].suffix
    with open(foldername/"concat_list.txt", "w") as f:
      for seg in all_segs:
          f.write('file ' + str(seg.absolute()) + "\n")
    os.system(f"ffmpeg -f concat -safe 0 -i {foldername}/concat_list.txt -codec copy {foldername}/{final_filename}")

def cleanup_dirs():
  """
  Deletes all temporary directories created in the splicing and inference-output step
  """
  !rm -R {INFERENCE_OUTPUT_DIRNAME}
  !rm -R {SEGMENTS_DIRNAME}

def get_audio_files():
  audio_files = []
  for root, dirs, files in os.walk("/content"):
    for filename in files:
      file_extension = os.path.splitext(filename)[1]
      if file_extension.lower() in MUSIC_EXTENSIONS and "output" not in filename:
        audio_files.append(filename)
      
  return audio_files

def get_speakers():
  speakers = []
  for _,dirs,_ in os.walk(MODELS_DIR):
    for folder in dirs:
      cur_speaker = {}
      # Look for G_****.pth
      g = glob.glob(os.path.join(MODELS_DIR,folder,'G_*.pth'))
      if not len(g):
        continue
      cur_speaker["model_path"] = g[0]
      cur_speaker["model_folder"] = folder

      # Look for *.pt (clustering model)
      clst = glob.glob(os.path.join(MODELS_DIR,folder,'*.pt'))
      if not len(clst):
        cur_speaker["cluster_path"] = ""
      else:
        cur_speaker["cluster_path"] = clst[0]

      # Look for config.json
      cfg = glob.glob(os.path.join(MODELS_DIR,folder,'*.json'))
      if not len(cfg):
        continue
      cur_speaker["cfg_path"] = cfg[0]
      with open(cur_speaker["cfg_path"]) as f:
        try:
          cfg_json = json.loads(f.read())
        except Exception as e:
          print("Malformed config json in "+folder)
        for name, i in cfg_json["spk"].items():
          cur_speaker["name"] = name
          cur_speaker["id"] = i
          if not name.startswith('.'):
            speakers.append(copy.copy(cur_speaker))

    return sorted(speakers, key=lambda x:x["name"].lower())

class InferenceGui():
  def __init__(self):
    self.speakers = get_speakers()
    self.speaker_list = [x["name"] for x in self.speakers]
    self.speaker_box = widgets.Dropdown(
        options = self.speaker_list,
        description="AI Model"
    )
    display(self.speaker_box)

    self.audio_files = get_audio_files()
    self.audio_files_box = widgets.Dropdown(
        options = self.audio_files,
        description="Audio File"
    )
    display(self.audio_files_box)

    self.f0_methods = ["crepe", "crepe-tiny", "parselmouth", "dio", "harvest"]
    self.f0_methods_box = widgets.Dropdown(options = self.f0_methods, description="F0 Method")
    display(self.f0_methods_box)

    def convert_cb(btn):
      self.convert()

    self.convert_btn = widgets.Button(description="Convert")
    self.convert_btn.on_click(convert_cb)
    self.clean_btn = widgets.Button(description="Delete all audio files")

    self.trans_tx = widgets.IntSlider(
      value=0,
      min=-12,
      max=12,
      step=1,
      description='Transpose',
      disabled=False,
      continuous_update=False,
      orientation='horizontal',
      readout=True,
      readout_format='d'
    )
    self.cluster_ratio_tx = widgets.FloatSlider(
      value=0,
      min=0,
      max=1.0,
      step=0.05,
      description='Cluster Ratio',
      disabled=False,
      continuous_update=False,
      orientation='horizontal',
      readout=True,
    )
    self.noise_scale_tx = widgets.FloatSlider(
      value=.4,
      min=-2,
      max=2,
      step=.4,
      description='Noise Scale',
      disabled=False,
      continuous_update=False,
      orientation='horizontal',
      readout=True,
    )

    display(self.trans_tx)
    display(self.noise_scale_tx)
    display(self.cluster_ratio_tx)
    display(self.convert_btn)

  def convert(self):
    speaker = next(x for x in self.speakers if x["name"] == 
          self.speaker_box.value)
    model_path = os.path.join(os.getcwd(),speaker["model_path"])
    config_path = os.path.join(os.getcwd(),speaker["cfg_path"])
    cluster_path = os.path.join(os.getcwd(),speaker["cluster_path"])
    file_path = os.path.join(os.getcwd(), str(self.audio_files_box.value))
    f0_method = str(self.f0_methods_box.value)
    transpose = int(self.trans_tx.value)
    noise_scale = int(self.noise_scale_tx.value)
    cluster_ratio = float(self.cluster_ratio_tx.value)

    if not speaker:
      raise Exception("Please select an AI Model.")
    if not self.audio_files_box.value or self.audio_files_box.value == "":
      raise Exception("Please select an audio file to clone.")

    if os.path.exists(SEGMENTS_DIRNAME) or os.path.exists(INFERENCE_OUTPUT_DIRNAME):
      print(f"Previous {SEGMENTS_DIRNAME} and {INFERENCE_OUTPUT_DIRNAME} folders detected.")
      cleanup_dirs()

    # SLICE AUDIO
    slice_audio(file_path, SEGMENT_LENGTH)

    # PERFORM INFERENCE - MULTITHREADING
    os.makedirs("inference_output", exist_ok=True)
    all_segs_paths = sorted(Path(SEGMENTS_DIRNAME).glob("*"))
    threads = []
    ts0 = time.time()
    for seg_path in all_segs_paths:
      # t = threading.Thread(target=run_inference, args=(speaker, seg_path, f0_method, transpose, noise_scale, cluster_ratio))
      # threads.append(t)

      # t.start()
      run_inference(speaker, seg_path, f0_method, transpose, noise_scale, cluster_ratio)

    # for t in threads:
    #   t.join()

    final_filename = f"output{Path(file_path).suffix}"

    # CONCATENATE FILES IN INFERENCE OUTPUT DIR
    concatenate_segments(INFERENCE_OUTPUT_DIRNAME, final_filename)

    # MOVE FINAL CONCATENATED FILE TO TOP-LEVEL IN CURRENT DIR
    shutil.move(Path(INFERENCE_OUTPUT_DIRNAME, final_filename), Path(final_filename))

    # CLEAN UP
    cleanup_dirs()

    ts1 = time.time()
    print(f"\nDone! You can download your output file in the file explorer as '{final_filename}' or through the audio player below.")
    print(f"Total Time Elapsed: {ts1 - ts0} seconds")
    display(Audio(final_filename))

inference_gui = InferenceGui()

In [ ]:
#@title Optional: Open the file explorer and drag-and-drop an instrumental track named "instru.mp3". Then run the below cell.

from pydub import AudioSegment
from IPython.display import Audio, display

sound1 = AudioSegment.from_file("/content/output.mp3")#path to vocal
sound2 = AudioSegment.from_file("/content/instru.mp3")#path to instrument

combined = sound1.overlay(sound2)

combined.export("/content/mix.mp3", format='mp3')#output path
display(Audio("/content/mix.mp3"))